In [19]:
# import the desired packages
import numpy as np
import pandas as pd
import json
import plotly.graph_objects as go
import plotly.io as pio
pio.templates.default = "simple_white"

In [20]:
def map_new_to_old_style(sequence):
    types = []
    landmark_indexes = []
    for column in list(sequence.columns)[1:544]:
        parts = column.split("_")
        if len(parts) == 4:
            types.append(parts[1] + "_" + parts[2])
        else:
            types.append(parts[1])

        landmark_indexes.append(int(parts[-1]))

    data = {
        "frame": [],
        "type": [],
        "landmark_index": [],
        "x": [],
        "y": [],
        "z": []
    }

    for index, row in sequence.iterrows():
        data["frame"] += [int(row.frame)]*543
        data["type"] += types
        data["landmark_index"] += landmark_indexes

        for _type, landmark_index in zip(types, landmark_indexes):
            data["x"].append(row[f"x_{_type}_{landmark_index}"])
            data["y"].append(row[f"y_{_type}_{landmark_index}"])
            data["z"].append(row[f"z_{_type}_{landmark_index}"])

    return pd.DataFrame.from_dict(data)

# assign desired colors to landmarks
def assign_color(row):
    if row == 'face':
        return 'red'
    elif 'hand' in row:
        return 'dodgerblue'
    else:
        return 'green'

# specifies the plotting order
def assign_order(row):
    if row.type == 'face':
        return row.landmark_index + 101
    elif row.type == 'pose':
        return row.landmark_index + 30
    elif row.type == 'left_hand':
        return row.landmark_index + 80
    else:
        return row.landmark_index

def visualise2d_landmarks(parquet_df, title=""):
    connections = [  
        [0, 1, 2, 3, 4,],
        [0, 5, 6, 7, 8],
        [0, 9, 10, 11, 12],
        [0, 13, 14, 15, 16],
        [0, 17, 18, 19, 20],

        
        [38, 36, 35, 34, 30, 31, 32, 33, 37],
        [40, 39],
        [52, 46, 50, 48, 46, 44, 42, 41, 43, 45, 47, 49, 45, 51],
        [42, 54, 56, 58, 60, 62, 58],
        [41, 53, 55, 57, 59, 61, 57],
        [54, 53],

        
        [80, 81, 82, 83, 84, ],
        [80, 85, 86, 87, 88],
        [80, 89, 90, 91, 92],
        [80, 93, 94, 95, 96],
        [80, 97, 98, 99, 100], ]

    parquet_df = map_new_to_old_style(parquet_df)
    frames = sorted(set(parquet_df.frame))
    first_frame = min(frames)
    parquet_df['color'] = parquet_df.type.apply(lambda row: assign_color(row))
    parquet_df['plot_order'] = parquet_df.apply(lambda row: assign_order(row), axis=1)
    first_frame_df = parquet_df[parquet_df.frame == first_frame].copy()
    first_frame_df = first_frame_df.sort_values(["plot_order"]).set_index('plot_order')


    frames_l = []
    for frame in frames:
        filtered_df = parquet_df[parquet_df.frame == frame].copy()
        filtered_df = filtered_df.sort_values(["plot_order"]).set_index("plot_order")
        traces = [go.Scatter(
            x=filtered_df['x'],
            y=filtered_df['y'],
            mode='markers',
            marker=dict(
                color=filtered_df.color,
                size=9))]

        for i, seg in enumerate(connections):
            trace = go.Scatter(
                    x=filtered_df.loc[seg]['x'],
                    y=filtered_df.loc[seg]['y'],
                    mode='lines',
            )
            traces.append(trace)
        frame_data = go.Frame(data=traces, traces = [i for i in range(17)])
        frames_l.append(frame_data)

    traces = [go.Scatter(
        x=first_frame_df['x'],
        y=first_frame_df['y'],
        mode='markers',
        marker=dict(
            color=first_frame_df.color,
            size=9
        )
    )]
    for i, seg in enumerate(connections):
        trace = go.Scatter(
            x=first_frame_df.loc[seg]['x'],
            y=first_frame_df.loc[seg]['y'],
            mode='lines',
            line=dict(
                color='black',
                width=2
            )
        )
        traces.append(trace)
    fig = go.Figure(
        data=traces,
        frames=frames_l
    )


    fig.update_layout(
        width=500,
        height=800,
        scene={
            'aspectmode': 'data',
        },
        updatemenus=[
            {
                "buttons": [
                    {
                        "args": [None, {"frame": {"duration": 100,
                                                  "redraw": True},
                                        "fromcurrent": True,
                                        "transition": {"duration": 0}}],
                        "label": "&#9654;",
                        "method": "animate",
                    },

                ],
                "direction": "left",
                "pad": {"r": 100, "t": 100},
                "font": {"size":30},
                "type": "buttons",
                "x": 0.1,
                "y": 0,
            }
        ],
    )
    camera = dict(
        up=dict(x=0, y=-1, z=0),
        eye=dict(x=0, y=0, z=2.5)
    )
    fig.update_layout(title_text=title, title_x=0.5)
    fig.update_layout(scene_camera=camera, showlegend=False)
    fig.update_layout(xaxis = dict(visible=False),
            yaxis = dict(visible=False),
    )
    fig.update_yaxes(autorange="reversed")

    fig.show()


def get_phrase(df, file_id, sequence_id):
    return df[
        np.logical_and(
            df.file_id == file_id, 
            df.sequence_id == sequence_id
        )
    ].phrase.iloc[0]

In [3]:
train = pd.read_csv('/kaggle/input/asl-fingerspelling/train.csv')
print(train.shape)
train.head()

(67208, 5)


path  file_id  sequence_id  participant_id  \
0  train_landmarks/5414471.parquet  5414471   1816796431             217   
1  train_landmarks/5414471.parquet  5414471   1816825349             107   
2  train_landmarks/5414471.parquet  5414471   1816909464               1   
3  train_landmarks/5414471.parquet  5414471   1816967051              63   
4  train_landmarks/5414471.parquet  5414471   1817123330              89   

                      phrase  
0               3 creekhouse  
1            scales/kuhaylah  
2        1383 william lanier  
3          988 franklin lane  
4  6920 northeast 661st road

In [4]:
train.describe()

file_id   sequence_id  participant_id
count  6.720800e+04  6.720800e+04    67208.000000
mean   1.094448e+09  1.072696e+09      119.758154
std    6.395616e+08  6.177372e+08       74.330468
min    5.414471e+06  7.109500e+04        0.000000
25%    5.277082e+08  5.376519e+08       63.000000
50%    1.099408e+09  1.074387e+09      113.000000
75%    1.662743e+09  1.605592e+09      178.000000
max    2.118949e+09  2.147465e+09      254.000000

In [15]:
sequence_id = 1816796431
file_id = 5414471
parquet_file_path = f'/kaggle/input/asl-fingerspelling/train_landmarks/{file_id}.parquet'
sign = pd.read_parquet(parquet_file_path)
sign

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
1816796431       0  0.710588  0.699951  0.705657  0.691768  0.699669   
1816796431       1  0.709525  0.697582  0.703713  0.691016  0.697576   
1816796431       2  0.711059  0.700858  0.706272  0.693285  0.700825   
1816796431       3  0.712799  0.702518  0.707840  0.694899  0.702445   
1816796431       4  0.712349  0.705451  0.709918  0.696006  0.705180   
...            ...       ...       ...       ...       ...       ...   
1848182207     296  0.657136  0.635888  0.643259  0.619031  0.633084   
1848182207     297  0.655706  0.635570  0.642730  0.618637  0.632830   
1848182207     298  0.653681  0.636057  0.643054  0.618643  0.633258   
1848182207     299  0.654293  0.635543  0.642558  0.617969  0.632699   
1848182207     300  0.655109  0.634491  0.641743  0.617779  0.631771   

             x_face_5  x_face_6  x_face_7  x_face_8  ...  z_right_hand_11  \
sequence_id                                          ...                    
1816796431   0.701980  0.709724  0.610405  0.712660  ...        -0.245855   
1816796431   0.700467  0.709796  0.616540  0.713729  ...              NaN   
1816796431   0.703319  0.711549  0.615606  0.715143  ...              NaN   
1816796431   0.704794  0.712483  0.625044  0.715677  ...        -0.370770   
1816796431   0.706928  0.712685  0.614356  0.714875  ...              NaN   
...               ...       ...       ...       ...  ...              ...   
1848182207   0.631827  0.630708  0.533120  0.626672  ...        -0.143147   
1848182207   0.631554  0.630344  0.531868  0.626445  ...              NaN   
1848182207   0.631800  0.630059  0.531178  0.625990  ...              NaN   
1848182207   0.631167  0.629263  0.531019  0.625069  ...              NaN   
1848182207   0.630562  0.629580  0.533534  0.626065  ...        -0.196495   

             z_right_hand_12  z_right_hand_13  z_right_hand_14  \
sequence_id                                                      
1816796431         -0.269148        -0.129743        -0.251501   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.408097        -0.185217        -0.325494   
1816796431               NaN              NaN              NaN   
...                      ...              ...              ...   
1848182207         -0.139659        -0.066276        -0.130910   
1848182207               NaN              NaN              NaN   
1848182207               NaN              NaN              NaN   
1848182207               NaN              NaN              NaN   
1848182207         -0.202258        -0.101019        -0.179127   

             z_right_hand_15  z_right_hand_16  z_right_hand_17  \
sequence_id                                                      
1816796431         -0.278687        -0.266530        -0.152852   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.343373        -0.328294        -0.203126   
1816796431               NaN              NaN              NaN   
...                      ...              ...              ...   
1848182207         -0.127341        -0.106674        -0.083439   
1848182207               NaN              NaN              NaN   
1848182207               NaN              NaN              NaN   
1848182207               NaN              NaN              NaN   
1848182207         -0.182757        -0.169923        -0.116275   

             z_right_hand_18  z_right_hand_19  z_right_hand_20  
sequence_id                                                     
1816796431         -0.257519        -0.275822        -0.266876  
1816796431               NaN              NaN              NaN  
1816796431               NaN              NaN              NaN  
1816796431         -0.315719   

In [11]:
(sign.index.nunique())

1000

In [18]:
sequence = sign[sign.index == sequence_id]
sequence

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
1816796431       0  0.710588  0.699951  0.705657  0.691768  0.699669   
1816796431       1  0.709525  0.697582  0.703713  0.691016  0.697576   
1816796431       2  0.711059  0.700858  0.706272  0.693285  0.700825   
1816796431       3  0.712799  0.702518  0.707840  0.694899  0.702445   
1816796431       4  0.712349  0.705451  0.709918  0.696006  0.705180   
...            ...       ...       ...       ...       ...       ...   
1816796431     118  0.700922  0.689774  0.695984  0.679756  0.688836   
1816796431     119  0.700576  0.692017  0.697875  0.682405  0.691249   
1816796431     120  0.700621  0.690338  0.696792  0.680982  0.689429   
1816796431     121  0.698651  0.693153  0.699358  0.683020  0.692136   
1816796431     122  0.698450  0.691408  0.697766  0.681728  0.690405   

             x_face_5  x_face_6  x_face_7  x_face_8  ...  z_right_hand_11  \
sequence_id                                          ...                    
1816796431   0.701980  0.709724  0.610405  0.712660  ...        -0.245855   
1816796431   0.700467  0.709796  0.616540  0.713729  ...              NaN   
1816796431   0.703319  0.711549  0.615606  0.715143  ...              NaN   
1816796431   0.704794  0.712483  0.625044  0.715677  ...        -0.370770   
1816796431   0.706928  0.712685  0.614356  0.714875  ...              NaN   
...               ...       ...       ...       ...  ...              ...   
1816796431   0.690414  0.696533  0.596424  0.697664  ...              NaN   
1816796431   0.692938  0.699178  0.598221  0.700476  ...              NaN   
1816796431   0.691177  0.697816  0.599110  0.699297  ...              NaN   
1816796431   0.693553  0.699259  0.599576  0.700144  ...              NaN   
1816796431   0.691932  0.697955  0.601320  0.698955  ...        -0.562035   

             z_right_hand_12  z_right_hand_13  z_right_hand_14  \
sequence_id                                                      
1816796431         -0.269148        -0.129743        -0.251501   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.408097        -0.185217        -0.325494   
1816796431               NaN              NaN              NaN   
...                      ...              ...              ...   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.660525        -0.267866        -0.402139   

             z_right_hand_15  z_right_hand_16  z_right_hand_17  \
sequence_id                                                      
1816796431         -0.278687        -0.266530        -0.152852   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.343373        -0.328294        -0.203126   
1816796431               NaN              NaN              NaN   
...                      ...              ...              ...   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431               NaN              NaN              NaN   
1816796431         -0.499361        -0.567256        -0.253603   

             z_right_hand_18  z_right_hand_19  z_right_hand_20  
sequence_id                                                     
1816796431         -0.257519        -0.275822        -0.266876  
1816796431               NaN              NaN              NaN  
1816796431               NaN              NaN              NaN  
1816796431         -0.315719   

In [22]:
sequence_phrase = get_phrase(train, file_id, sequence_id)
visualise2d_landmarks(sequence, f"Phrase: {sequence_phrase}")

In [23]:
supplemental_df = pd.read_csv('/kaggle/input/asl-fingerspelling/supplemental_metadata.csv')
supplemental_df

path     file_id  sequence_id  \
0        supplemental_landmarks/33432165.parquet    33432165   1535467051   
1        supplemental_landmarks/33432165.parquet    33432165   1535499058   
2        supplemental_landmarks/33432165.parquet    33432165   1535530550   
3        supplemental_landmarks/33432165.parquet    33432165   1535545499   
4        supplemental_landmarks/33432165.parquet    33432165   1535585216   
...                                          ...         ...          ...   
52953  supplemental_landmarks/2100073719.parquet  2100073719   1090866442   
52954  supplemental_landmarks/2100073719.parquet  2100073719   1090966452   
52955  supplemental_landmarks/2100073719.parquet  2100073719   1091005846   
52956  supplemental_landmarks/2100073719.parquet  2100073719   1091011550   
52957  supplemental_landmarks/2100073719.parquet  2100073719   1091039755   

       participant_id                                    phrase  
0                 251         coming up with killer sound bites  
1                 239                we better investigate this  
2                 245          interesting observation was made  
3                  38              victims deserve more redress  
4                 254  knee bone is connected to the thigh bone  
...               ...                                       ...  
52953             239                 want to join us for lunch  
52954              95          this phenomenon will never occur  
52955              40                    the winner of the race  
52956             241                are you sure you want this  
52957             122       every saturday he folds the laundry  

[52958 rows x 5 columns]

In [26]:
sequence_id = 970395433
file_id = 1047404576
parquet_file_path = f'/kaggle/input/asl-fingerspelling/supplemental_landmarks/{file_id}.parquet'
sign = pd.read_parquet(parquet_file_path)
sign

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
930713929        0  0.756704  0.760945  0.760907  0.765285  0.765273   
930713929        1  0.754887  0.756969  0.757916  0.762007  0.761144   
930713929        2  0.747261  0.756341  0.756940  0.760954  0.760542   
930713929        3  0.751132  0.752736  0.753472  0.758956  0.757342   
930713929        4  0.748911  0.756597  0.756251  0.762455  0.761364   
...            ...       ...       ...       ...       ...       ...   
970395433      189  0.230609  0.226497  0.228425  0.211204  0.225883   
970395433      190  0.232066  0.227038  0.229065  0.211432  0.226396   
970395433      191  0.232894  0.229721  0.231461  0.213858  0.229098   
970395433      192  0.234138  0.230035  0.231696  0.213770  0.229365   
970395433      193  0.235482  0.229980  0.231763  0.213935  0.229303   

             x_face_5  x_face_6  x_face_7  x_face_8  ...  z_right_hand_11  \
sequence_id                                          ...                    
930713929    0.773185  0.793938  0.679266  0.807716  ...        -0.210778   
930713929    0.769312  0.791224  0.678670  0.805400  ...              NaN   
930713929    0.768563  0.789545  0.678402  0.803076  ...              NaN   
930713929    0.766016  0.788622  0.678341  0.803078  ...              NaN   
930713929    0.769904  0.792037  0.680310  0.806611  ...        -0.102712   
...               ...       ...       ...       ...  ...              ...   
970395433    0.225883  0.226804  0.105193  0.226612  ...              NaN   
970395433    0.226318  0.226908  0.105535  0.226550  ...              NaN   
970395433    0.228896  0.229012  0.106132  0.228482  ...              NaN   
970395433    0.229089  0.228936  0.106346  0.228138  ...              NaN   
970395433    0.229028  0.228871  0.105778  0.228036  ...              NaN   

             z_right_hand_12  z_right_hand_13  z_right_hand_14  \
sequence_id                                                      
930713929          -0.233004        -0.125909        -0.189850   
930713929                NaN              NaN              NaN   
930713929                NaN              NaN              NaN   
930713929                NaN              NaN              NaN   
930713929          -0.107486        -0.064889        -0.102419   
...                      ...              ...              ...   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   

             z_right_hand_15  z_right_hand_16  z_right_hand_17  \
sequence_id                                                      
930713929          -0.211914        -0.221384        -0.143339   
930713929                NaN              NaN              NaN   
930713929                NaN              NaN              NaN   
930713929                NaN              NaN              NaN   
930713929          -0.091282        -0.081263        -0.080556   
...                      ...              ...              ...   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   

             z_right_hand_18  z_right_hand_19  z_right_hand_20  
sequence_id                                                     
930713929          -0.194008        -0.206992        -0.213322  
930713929                NaN              NaN              NaN  
930713929                NaN              NaN              NaN  
930713929                NaN   

In [27]:
sequence = sign[sign.index == sequence_id]
sequence

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
970395433        0  0.281422  0.281852  0.281922  0.271682  0.282949   
970395433        1  0.281828  0.282806  0.283046  0.273077  0.283970   
970395433        2  0.283267  0.283481  0.283733  0.273681  0.284600   
970395433        3  0.285051  0.284169  0.284061  0.274522  0.285364   
970395433        4  0.284558  0.284670  0.284554  0.274068  0.285697   
...            ...       ...       ...       ...       ...       ...   
970395433      189  0.230609  0.226497  0.228425  0.211204  0.225883   
970395433      190  0.232066  0.227038  0.229065  0.211432  0.226396   
970395433      191  0.232894  0.229721  0.231461  0.213858  0.229098   
970395433      192  0.234138  0.230035  0.231696  0.213770  0.229365   
970395433      193  0.235482  0.229980  0.231763  0.213935  0.229303   

             x_face_5  x_face_6  x_face_7  x_face_8  ...  z_right_hand_11  \
sequence_id                                          ...                    
970395433    0.284955  0.290224  0.168223  0.293704  ...              NaN   
970395433    0.286183  0.292006  0.171258  0.295807  ...              NaN   
970395433    0.286733  0.292300  0.172196  0.295933  ...              NaN   
970395433    0.287511  0.293120  0.171812  0.296879  ...              NaN   
970395433    0.287385  0.291707  0.171875  0.294734  ...              NaN   
...               ...       ...       ...       ...  ...              ...   
970395433    0.225883  0.226804  0.105193  0.226612  ...              NaN   
970395433    0.226318  0.226908  0.105535  0.226550  ...              NaN   
970395433    0.228896  0.229012  0.106132  0.228482  ...              NaN   
970395433    0.229089  0.228936  0.106346  0.228138  ...              NaN   
970395433    0.229028  0.228871  0.105778  0.228036  ...              NaN   

             z_right_hand_12  z_right_hand_13  z_right_hand_14  \
sequence_id                                                      
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
...                      ...              ...              ...   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   

             z_right_hand_15  z_right_hand_16  z_right_hand_17  \
sequence_id                                                      
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
...                      ...              ...              ...   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   
970395433                NaN              NaN              NaN   

             z_right_hand_18  z_right_hand_19  z_right_hand_20  
sequence_id                                                     
970395433                NaN              NaN              NaN  
970395433                NaN              NaN              NaN  
970395433                NaN              NaN              NaN  
970395433                NaN   

In [29]:
sequence_phrase = get_phrase(supplemental_df, file_id, sequence_id)
visualise2d_landmarks(sequence, f"Phrase: {sequence_phrase}")